In [1]:
from __future__ import print_function, division

import plotly.graph_objects as go
import numpy as np
import scipy.spatial.distance
import math
import random

import os
import glob
import torch
import pandas as pd
from skimage import io, transform
import numpy as np
import matplotlib.pyplot as plt
from torch.utils.data import Dataset, DataLoader, WeightedRandomSampler
from torchvision import transforms, utils
from torch.utils.data.dataset import random_split

In [2]:
root_dir = '/home/trojan/skia_projects/3d_facial_segmentation/part_segmentation/pointnet/pointnet'

sample_points_train = 16000
sample_points_valid = 9595

In [3]:
import random

def read_pts(file):
    verts = np.genfromtxt(file)
    #return utils.cent_norm(verts)
    return verts

def read_seg(file):
    verts = np.genfromtxt(file, dtype= (int))
    return verts

def sample_2000(pts, pts_cat):    
    res1 = np.concatenate((pts,np.reshape(pts_cat, (pts_cat.shape[0], 1))), axis= 1)
    res = np.asarray(random.choices(res1, weights=None, cum_weights=None, k=2000))
    images = res[:, 0:3]
    categories = res[:, 3]
    categories-=np.ones(categories.shape)
    return images, categories

def read_data(file):
    data = np.genfromtxt(file).astype(np.float64)
    img = data[:, 0:3]
    seg = data[:, -1].astype(np.int64)
    return img, seg

def Normalize(pointcloud):
    norm_pointcloud = pointcloud - np.mean(pointcloud, axis=0)
    norm_pointcloud /= np.max(np.linalg.norm(norm_pointcloud, axis=1))

    return  norm_pointcloud

class RandRotation_z(object):
    def __call__(self, pointcloud):
        assert len(pointcloud.shape)==2

        theta = random.random() * 2. * math.pi
        rot_matrix = np.array([[ math.cos(theta), -math.sin(theta),    0],
                               [ math.sin(theta),  math.cos(theta),    0],
                               [0,                             0,      1]])
        
        rot_pointcloud = rot_matrix.dot(pointcloud.T).T
        return  rot_pointcloud
    
class Random_Noise(object):
    def __call__(self, pointcloud):
        assert len(pointcloud.shape)==2

        noise = np.random.normal(0, 0.02, (pointcloud.shape))
    
        noisy_pointcloud = pointcloud + noise
        return  noisy_pointcloud
    
    
def rotation_z(pointcloud, theta):
    rot_matrix = np.array([[ math.cos(theta), -math.sin(theta), 0],
                               [ math.sin(theta),  math.cos(theta), 0],
                               [0, 0, 1]])
        
    rot_pointcloud = rot_matrix.dot(pointcloud.T).T
    return  rot_pointcloud

def random_noise(pointcloud):
    noise = np.random.normal(0, 0.02, (pointcloud.shape))
    
    noisy_pointcloud = pointcloud + noise
    return  noisy_pointcloud

In [4]:
class Data(Dataset):
    """Face Landmarks dataset."""

    def __init__(self, root_dir, valid=False, transform=None):
        
        self.root_dir = root_dir
        self.files = []
        self.valid=valid

        newdir = root_dir + '/datasets/head_data/train_balanced/'

        for file in os.listdir(newdir):
            o = {}
            o['path'] = newdir + file
            self.files.append(o)
       

    def __len__(self):
        return len(self.files)

    def __getitem__(self, idx):
        path = self.files[idx]['path']
        with open(path, 'r') as f:
            image1, category1 = read_data(f)
            
        choice = np.random.choice(len(category1), sample_points_train, replace=True)

        image2 = image1[choice, :]
        category2 = category1[choice]
        
        image2 = Normalize(image2)
        #image2, category2 = sample_2000(image1, category1)
#         if not self.valid:
#             theta = random.random()*360
#             image2 = rotation_z(random_noise(image2), theta)
        
        return {'image': np.array(image2, dtype="float32"), 'category': category2.astype(int)}
    
class DataValid(Dataset):
    """Face Landmarks dataset."""

    def __init__(self, root_dir, valid=False, transform=None):
        
        self.root_dir = root_dir
        self.files = []
        self.valid=valid

        newdir = root_dir + '/datasets/head_data/train/'

        for file in os.listdir(newdir):
            o = {}
            o['path'] = newdir + file
            self.files.append(o)
       

    def __len__(self):
        return len(self.files)

    def __getitem__(self, idx):
        path = self.files[idx]['path']
        with open(path, 'r') as f:
            image1, category1 = read_data(f)
            
        choice = np.random.choice(len(category1), sample_points_valid, replace=True)

        image2 = image1[choice, :]
        category2 = category1[choice]
        
        image2 = Normalize(image2)
        #image2, category2 = sample_2000(image1, category1)
#         if not self.valid:
#             theta = random.random()*360
#             image2 = rotation_z(random_noise(image2), theta)
        
        return {'image': np.array(image2, dtype="float32"), 'category': category2.astype(int)}

In [5]:
dset = Data(root_dir , transform=None)
dset_valid = DataValid(root_dir , transform=None)
print('######### Train dataset class created #########')
print('Number of images: ', len(dset))
print('Sample image shape: ', dset[0]['image'].shape)
print('\n')
print('######### Valid dataset class created #########')
print('Number of images: ', len(dset_valid))
print('Sample image shape: ', dset_valid[0]['image'].shape)

train_loader = DataLoader(dataset=dset, batch_size=2, drop_last=True)
val_loader = DataLoader(dataset=dset_valid, batch_size=2, drop_last=True)

######### Train dataset class created #########
Number of images:  7
Sample image shape:  (16000, 3)


######### Valid dataset class created #########
Number of images:  7
Sample image shape:  (9595, 3)


In [6]:
print(dset[1])

{'image': array([[ 0.22373399, -0.6628274 ,  0.14027798],
       [ 0.332348  ,  0.6397054 , -0.01524027],
       [ 0.54033923, -0.17730267, -0.15879187],
       ...,
       [-0.00960696, -0.67250603, -0.50524414],
       [ 0.48263046,  0.5187615 , -0.23005316],
       [ 0.20910403, -0.38744873,  0.43022606]], dtype=float32), 'category': array([0, 0, 1, ..., 0, 0, 0])}


In [7]:
print(len(dset))

7


In [8]:
import torch
import torch.nn as nn
import numpy as np
import torch.nn.functional as F

class Tnet(nn.Module):
    def __init__(self, k=3):
        super().__init__()
        self.k=k
        self.conv1 = nn.Conv1d(k,64,1)
        self.conv2 = nn.Conv1d(64,128,1)
        self.conv3 = nn.Conv1d(128,1024,1)
        self.fc1 = nn.Linear(1024,512)
        self.fc2 = nn.Linear(512,256)
        self.fc3 = nn.Linear(256,k*k)

        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(1024)
        self.bn4 = nn.BatchNorm1d(512)
        self.bn5 = nn.BatchNorm1d(256)
       

    def forward(self, input):
    # input.shape == (bs,n,3)
        bs = input.size(0)
        xb = F.relu(self.bn1(self.conv1(input)))
        xb = F.relu(self.bn2(self.conv2(xb)))
        xb = F.relu(self.bn3(self.conv3(xb)))
        pool = nn.MaxPool1d(xb.size(-1))(xb)
        flat = nn.Flatten(1)(pool)
        xb = F.relu(self.bn4(self.fc1(flat)))
        xb = F.relu(self.bn5(self.fc2(xb)))

        #initialize as identity
        init = torch.eye(self.k, requires_grad=True).repeat(bs,1,1)
        if xb.is_cuda:
            init=init.cuda()
        matrix = self.fc3(xb).view(-1,self.k,self.k) + init
        return matrix


class Transform(nn.Module):
    def __init__(self):
        super().__init__()
        self.input_transform = Tnet(k=3)
        self.feature_transform = Tnet(k=128)
        self.fc1 = nn.Conv1d(3,64,1)
        self.fc2 = nn.Conv1d(64,128,1) 
        self.fc3 = nn.Conv1d(128,128,1)
        self.fc4 = nn.Conv1d(128,512,1)
        self.fc5 = nn.Conv1d(512,2048,1)


        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(128)
        self.bn4 = nn.BatchNorm1d(512)
        self.bn5 = nn.BatchNorm1d(2048)

    def forward(self, input):
        n_pts = input.size()[2]
        matrix3x3 = self.input_transform(input)
        xb = torch.bmm(torch.transpose(input,1,2), matrix3x3).transpose(1,2)
        outs = []

        out1 = F.relu(self.bn1(self.fc1(xb)))
        outs.append(out1)
        out2 = F.relu(self.bn2(self.fc2(out1)))
        outs.append(out2)
        out3 = F.relu(self.bn3(self.fc3(out2)))
        outs.append(out3)
        matrix128x128 = self.feature_transform(out3)

        out4 = torch.bmm(torch.transpose(out3,1,2), matrix128x128).transpose(1,2) 
        outs.append(out4)
        out5 = F.relu(self.bn4(self.fc4(out4)))
        outs.append(out5)

        xb = self.bn5(self.fc5(out5))

        xb = nn.MaxPool1d(xb.size(-1))(xb)
        out6 = nn.Flatten(1)(xb).repeat(n_pts,1,1).transpose(0,2).transpose(0,1)#.repeat(1, 1, n_pts)
        outs.append(out6)


        return outs, matrix3x3, matrix128x128


class PointNetSeg(nn.Module):
    def __init__(self, classes = 10):
        super().__init__()
        self.transform = Transform()

        self.fc1 = nn.Conv1d(3008,256,1) 
        self.fc2 = nn.Conv1d(256,256,1) 
        self.fc3 = nn.Conv1d(256,128,1) 
        self.fc4 = nn.Conv1d(128,2,1) 
        

        self.bn1 = nn.BatchNorm1d(256)
        self.bn2 = nn.BatchNorm1d(256)
        
        self.bn3 = nn.BatchNorm1d(128)
        self.bn4 = nn.BatchNorm1d(2)
        
        self.logsoftmax = nn.LogSoftmax(dim=1)
        

    def forward(self, input):
        inputs, matrix3x3, matrix128x128 = self.transform(input)
        stack = torch.cat(inputs,1)
        
        xb = F.relu(self.bn1(self.fc1(stack)))
       
        xb = F.relu(self.bn2(self.fc2(xb)))
    
        xb = F.relu(self.bn3(self.fc3(xb)))
        
        output = F.relu(self.bn4(self.fc4(xb)))
        
        return self.logsoftmax(output), matrix3x3, matrix128x128

In [9]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


In [10]:
pointnet = PointNetSeg()

In [11]:
pointnet.to(device)

PointNetSeg(
  (transform): Transform(
    (input_transform): Tnet(
      (conv1): Conv1d(3, 64, kernel_size=(1,), stride=(1,))
      (conv2): Conv1d(64, 128, kernel_size=(1,), stride=(1,))
      (conv3): Conv1d(128, 1024, kernel_size=(1,), stride=(1,))
      (fc1): Linear(in_features=1024, out_features=512, bias=True)
      (fc2): Linear(in_features=512, out_features=256, bias=True)
      (fc3): Linear(in_features=256, out_features=9, bias=True)
      (bn1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn3): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn4): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn5): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (feature_transform): Tnet(
      (conv1): Conv1d(128, 64, kernel_size

In [12]:
optimizer = torch.optim.Adam(pointnet.parameters(), lr=0.001)

In [13]:
def pointnetloss(outputs, labels, m3x3, m128x128, alpha = 0.0001):
    criterion = torch.nn.NLLLoss()
    bs=outputs.size(0)
    id3x3 = torch.eye(3, requires_grad=True).repeat(bs,1,1)
    id128x128 = torch.eye(128, requires_grad=True).repeat(bs,1,1)
    if outputs.is_cuda:
        id3x3=id3x3.cuda()
        id128x128=id128x128.cuda()
    diff3x3 = id3x3-torch.bmm(m3x3,m3x3.transpose(1,2))
    diff128x128 = id128x128-torch.bmm(m128x128,m128x128.transpose(1,2))
    return criterion(outputs, labels) + alpha * (torch.norm(diff3x3)+torch.norm(diff128x128)) / float(bs)

In [14]:
def train(model, train_loader, val_loader=None,  epochs=500, save=True):
    for epoch in range(1, epochs+1): 
        pointnet.train()
        running_loss = 0.0
        for i, data in enumerate(train_loader, 0):
            inputs, labels = data['image'].to(device), data['category'].to(device)
            optimizer.zero_grad()
            outputs, m3x3, m64x64 = pointnet(inputs.transpose(1,2))

            loss = pointnetloss(outputs, labels, m3x3, m64x64)
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            if epoch % 10 == 0:    # print every 10 epochs
                    print('[%d, %5d] loss: %.3f' %
                        (epoch, i + 1, running_loss / 10))
                    running_loss = 0.0

        pointnet.eval()
        correct = total = 0

        # validation
        if val_loader:
            with torch.no_grad():
                for data in val_loader:
                    inputs, labels = data['image'].to(device), data['category'].to(device)
                    outputs, __, __ = pointnet(inputs.transpose(1,2))
                    _, predicted = torch.max(outputs.data, 1)
                    total += labels.size(0) * labels.size(1) ##
                    correct += (predicted == labels).sum().item()
            val_acc = 100 * correct / total
            
            if epoch % 10 == 0: 
                print('Valid accuracy: %d %%' % val_acc)

                # save the model
                if save:
                    torch.save(pointnet.state_dict(), root_dir+"/modelsSeg/"+str(epoch)) # +"_"+str(val_acc))

In [15]:
train(pointnet, train_loader, val_loader, save=True)

[10,     1] loss: 0.046
[10,     2] loss: 0.045
[10,     3] loss: 0.045
Valid accuracy: 69 %
[20,     1] loss: 0.041
[20,     2] loss: 0.041
[20,     3] loss: 0.041
Valid accuracy: 89 %
[30,     1] loss: 0.039
[30,     2] loss: 0.039
[30,     3] loss: 0.037
Valid accuracy: 90 %
[40,     1] loss: 0.037
[40,     2] loss: 0.037
[40,     3] loss: 0.036
Valid accuracy: 90 %
[50,     1] loss: 0.035
[50,     2] loss: 0.034
[50,     3] loss: 0.034
Valid accuracy: 90 %
[60,     1] loss: 0.034
[60,     2] loss: 0.034
[60,     3] loss: 0.033
Valid accuracy: 88 %
[70,     1] loss: 0.033
[70,     2] loss: 0.032
[70,     3] loss: 0.032
Valid accuracy: 90 %
[80,     1] loss: 0.032
[80,     2] loss: 0.031
[80,     3] loss: 0.030
Valid accuracy: 88 %
[90,     1] loss: 0.032
[90,     2] loss: 0.032
[90,     3] loss: 0.032
Valid accuracy: 87 %
[100,     1] loss: 0.030
[100,     2] loss: 0.029
[100,     3] loss: 0.029
Valid accuracy: 85 %
[110,     1] loss: 0.033
[110,     2] loss: 0.037
[110,     3] loss

In [17]:
dicts_dir = root_dir+"/modelsSeg/"
dict_list = os.listdir(dicts_dir)
dict_list = [int(x) for x in dict_list]
dict_list.sort()
print(dict_list)

model_path = os.path.join(dicts_dir, str(dict_list[len(dict_list)-1]))
print(model_path)

[10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, 120, 130, 140, 150, 160, 170, 180, 190, 200, 210, 220, 230, 240, 250, 260, 270, 280, 290, 300, 310, 320, 330, 340, 350, 360, 370, 380, 390, 400, 410, 420, 430, 440, 450, 460, 470, 480, 490, 500]
/home/trojan/skia_projects/3d_facial_segmentation/part_segmentation/pointnet/pointnet/modelsSeg/500


In [18]:
pointnet = PointNetSeg()

dicts_dir = root_dir+"/modelsSeg/"
dict_list = os.listdir(dicts_dir)
dict_list = [int(x) for x in dict_list]
dict_list.sort()
model_path = os.path.join(dicts_dir, str(dict_list[len(dict_list) - 1]))

pointnet.load_state_dict(torch.load(model_path))
pointnet.eval()

PointNetSeg(
  (transform): Transform(
    (input_transform): Tnet(
      (conv1): Conv1d(3, 64, kernel_size=(1,), stride=(1,))
      (conv2): Conv1d(64, 128, kernel_size=(1,), stride=(1,))
      (conv3): Conv1d(128, 1024, kernel_size=(1,), stride=(1,))
      (fc1): Linear(in_features=1024, out_features=512, bias=True)
      (fc2): Linear(in_features=512, out_features=256, bias=True)
      (fc3): Linear(in_features=256, out_features=9, bias=True)
      (bn1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn3): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn4): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn5): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (feature_transform): Tnet(
      (conv1): Conv1d(128, 64, kernel_size

In [29]:
batch = next(iter(val_loader))
pred = pointnet(batch['image'].transpose(1,2))
pred_np = np.array(torch.argmax(pred[0],1));
pred_np

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [49]:
idx = 1

In [50]:
batch['image'][idx].shape

torch.Size([9595, 3])

In [51]:
print(batch['category'][idx])

tensor([0, 0, 0,  ..., 0, 0, 0])


In [52]:
pred_np==np.array(batch['category'])

array([[ True, False,  True, ..., False,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True]])

In [53]:
acc = (pred_np==np.array(batch['category']))

In [54]:
resulting_acc = np.sum(acc, axis=1) / 9595

In [55]:
resulting_acc

array([0.89859302, 0.91912454])

In [56]:
pred_np[idx]

array([0, 0, 0, ..., 0, 0, 0])

In [57]:
################################################33
# Checking count

In [58]:
_list = list(pred_np[idx])

In [59]:
count_pred = _list.count(0)
print(count_pred)

9532


In [60]:
batch['category'][idx]

tensor([0, 0, 0,  ..., 0, 0, 0])

In [61]:
tmp = list(batch['category'][idx])

In [62]:
print(tmp)

[tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(1), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(1), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(1), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(1), tensor(1), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(1), tensor(0), tensor(1), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0), tensor(0)

In [63]:
count_orig = tmp.count(0)
print(count_orig)

8882


In [64]:
print(f"Predicted zeros: {count_pred}")
print(f"Original zeros: {count_orig}")

Predicted zeros: 9532
Original zeros: 8882


In [65]:
###################################################################33

In [66]:

x,y,z=np.array(batch['image'][idx]).T
c = np.array(batch['category'][idx]).T

fig = go.Figure(data=[go.Scatter3d(x=x, y=y, z=z, 
                                   mode='markers',
                                   marker=dict(
        size=30,
        color=c,                # set color to an array/list of desired values
        colorscale='Viridis',   # choose a colorscale
        opacity=1.0
    ))])
fig.update_traces(marker=dict(size=2,
                              line=dict(width=2,
                                        color='DarkSlateGrey')),
                  selector=dict(mode='markers'))
fig.show()



In [67]:

x,y,z=np.array(batch['image'][idx]).T
c = np.array(pred_np[idx]).T

fig = go.Figure(data=[go.Scatter3d(x=x, y=y, z=z, 
                                   mode='markers',
                                   marker=dict(
        size=30,
        color=c,                # set color to an array/list of desired values
        colorscale='Viridis',   # choose a colorscale
        opacity=1.0
    ))])
fig.update_traces(marker=dict(size=2,
                              line=dict(width=2,
                                        color='DarkSlateGrey')),
                  selector=dict(mode='markers'))
fig.show()



In [37]:
class TestData(Dataset):
    """Face Landmarks dataset."""

    def __init__(self, root_dir, valid=False, transform=None):
        
        self.root_dir = root_dir
        self.files = []
        self.valid=valid

        newdir = root_dir + '/datasets/head_data/test/'

        for file in os.listdir(newdir):
            o = {}
            o['path'] = newdir + file
            self.files.append(o)
       

    def __len__(self):
        return len(self.files)

    def __getitem__(self, idx):
        path = self.files[idx]['path']
        with open(path, 'r') as f:
            data = read_pts(f)
            image = data[:, 0:3]
            
        choice = np.random.choice(len(image), 9000, replace=True)

        image = image[choice, :]
        
        image = Normalize(image)
        
        #image2, category2 = sample_2000(image1, category1)
#         if not self.valid:
#             theta = random.random()*360
#             image2 = rotation_z(random_noise(image2), theta)
        
        return {'image': np.array(image, dtype="float32")}

In [38]:
test_dataset = TestData(root_dir , transform=None)

print('######### Dataset class created #########')
print('Number of images: ', len(test_dataset))
print('Sample image shape: ', test_dataset[0]['image'].shape)
#print('Sample image points categories', dset[0]['category'], end='\n\n')

test_loader = DataLoader(dataset=test_dataset, batch_size=1)

######### Dataset class created #########
Number of images:  1
Sample image shape:  (9000, 3)


In [39]:
batch_test = next(iter(test_loader))
pred = pointnet(batch_test['image'].transpose(1,2))
pred_np = np.array(torch.argmax(pred[0],1));
pred_np

array([[1, 1, 1, ..., 1, 1, 1]])

In [40]:
batch_test['image'][0].shape

torch.Size([9000, 3])

In [41]:
x,y,z=np.array(batch_test['image'][0]).T
c = np.array(pred_np[0]).T

fig = go.Figure(data=[go.Scatter3d(x=x, y=y, z=z, 
                                   mode='markers',
                                   marker=dict(
        size=30,
        color=c,                # set color to an array/list of desired values
        colorscale='Viridis',   # choose a colorscale
        opacity=1.0
    ))])
fig.update_traces(marker=dict(size=2,
                              line=dict(width=2,
                                        color='DarkSlateGrey')),
                  selector=dict(mode='markers'))
fig.show()